
$a_h(u_h, v_h) + b_h(v_h, p_h)-b_h(u_h, q_h)+ c_h(p_h, q_h)=\int_\Omega f\cdot v_hdx$

where the discrete bilinear form $a_h$ is defined by  \begin{align*}
a_h (u, v)& =\int_\Omega\nabla u:\nabla vdx + \sum\limits_{K\in\mathcal{T}}\int_{\partial K}\frac{\alpha}{h_K}(u-\bar{u})(v-\bar{v})ds\\
&\quad-\sum\limits_{K\in\mathcal{T}}\int_{\partial K} [(\nabla u\cdot n_K)(v-\bar{v}) + (u-\bar{u})(\nabla v\cdot n_K)]ds,
\end{align*} the discrete bilinear form $b_h$ by 
$$b_h(v,q) = -\int_\Omega q\nabla\cdot v dx + \sum\limits_{K\in \mathcal{T}}\int_{\partial K}(v-\bar{v})\cdot n\bar{q}ds,$$ and where
$c_h(q, r):=\sum\limits_{K\in \mathcal{T}}\int_{\partial K}h_K(q-\bar{q})(r-\bar{r})ds.$


In [21]:
import netgen.gui
from netgen.geom2d import unit_square
from ngsolve import *
from math import pi

mesh = Mesh(unit_square.GenerateMesh(maxh=0.2))
#mesh.Refine()

Draw(mesh)
mesh.nv, mesh.ne   # number of vertices & elements
#mesh.GetBoundaries()
k = 2
V = VectorL2(mesh,order=k, dirichlet ='left|right|top|bottom')
Q = L2(mesh,order=k-1)
Vbar = FacetFESpace(mesh, order = k, dirichlet= "bottom|right|top|left")
Qbar = FacetFESpace(mesh, order = k)  
X    = FESpace([V, Vbar, Vbar, Q, Qbar])

gfu = GridFunction(X)

(u, ubar1, ubar2, p, pbar)  = X.TrialFunction()
(v, vbar1, vbar2, q, qbar)  = X.TrialFunction()
n = specialcf.normal(mesh.dim) 
h = specialcf.mesh_size        
ubar = CoefficientFunction((ubar1, ubar2))
vbar = CoefficientFunction((vbar1, vbar2))
# Penalty parameter
eta=1
#gradient u, v
du = grad(u)
dv = grad(v)
#normal gradient
dudn=du*n
dvdn=dv*n
# Bilinear form
a = BilinearForm(X)
ah_dx = InnerProduct(du, dv)
ah_ds   = (eta/h)*(u-ubar)*(v-vbar)- InnerProduct(u-ubar,dvdn) - InnerProduct(dudn,v-vbar)

bh_dx = - p*div(v) + q*div(u)
bh_ds   = (v-vbar)*n*pbar - (u-ubar)*n*qbar

ch= h*(p-pbar)*(q-qbar)

a += (ah_dx + bh_dx)*dx
a += (ah_ds + bh_ds)*dx(element_boundary=True)
a += ch*dx(skeleton=True) # interface
a += ch*ds(skeleton=True) # boundary


# Linear form
f = LinearForm(X)


a.Assemble()
f.Assemble()


inv = a.mat.Inverse(freedofs=X.FreeDofs(), inverse="umfpack")
res = f.vec.CreateVector()
res.data = f.vec - a.mat*gfu.vec
gfu.vec.data += inv * res

NgException: SparseMatrixTM::AddElementMatrix: illegal dnumsin Assemble BilinearForm 'biform_from_py'
